In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/march-machine-learning-mania-2025/Conferences.csv
/kaggle/input/march-machine-learning-mania-2025/SeedBenchmarkStage1.csv
/kaggle/input/march-machine-learning-mania-2025/WNCAATourneyDetailedResults.csv
/kaggle/input/march-machine-learning-mania-2025/WRegularSeasonCompactResults.csv
/kaggle/input/march-machine-learning-mania-2025/MNCAATourneySeedRoundSlots.csv
/kaggle/input/march-machine-learning-mania-2025/MRegularSeasonDetailedResults.csv
/kaggle/input/march-machine-learning-mania-2025/MNCAATourneyCompactResults.csv
/kaggle/input/march-machine-learning-mania-2025/MGameCities.csv
/kaggle/input/march-machine-learning-mania-2025/WSecondaryTourneyCompactResults.csv
/kaggle/input/march-machine-learning-mania-2025/WGameCities.csv
/kaggle/input/march-machine-learning-mania-2025/MSeasons.csv
/kaggle/input/march-machine-learning-mania-2025/WNCAATourneySlots.csv
/kaggle/input/march-machine-learning-mania-2025/MSecondaryTourneyTeams.csv
/kaggle/input/march-machine-learning-mania-20

In [2]:
import pandas as pd
import numpy as np
from sklearn.model_selection import StratifiedKFold, cross_val_score
from sklearn.metrics import brier_score_loss
from xgboost import XGBClassifier
from catboost import CatBoostClassifier
from lightgbm import LGBMClassifier
from sklearn.ensemble import StackingClassifier
import optuna
from tqdm import tqdm
import os
import warnings
warnings.filterwarnings('ignore')
base_path = "/kaggle/input/march-machine-learning-mania-2025"
m_regular_season_file = os.path.join(base_path, "MRegularSeasonCompactResults.csv")
w_regular_season_file = os.path.join(base_path, "WRegularSeasonCompactResults.csv")
m_tourney_file = os.path.join(base_path, "MNCAATourneyCompactResults.csv")
w_tourney_file = os.path.join(base_path, "WNCAATourneyCompactResults.csv")
m_seeds_file = os.path.join(base_path, "MNCAATourneySeeds.csv")
w_seeds_file = os.path.join(base_path, "WNCAATourneySeeds.csv")
submission_file = os.path.join(base_path, "SampleSubmissionStage1.csv")
print("Veri setleri yükleniyor...")
try:
    df_m_regular = pd.read_csv(m_regular_season_file)
    df_w_regular = pd.read_csv(w_regular_season_file)
    df_m_tourney = pd.read_csv(m_tourney_file)
    df_w_tourney = pd.read_csv(w_tourney_file)
    df_m_seeds = pd.read_csv(m_seeds_file)
    df_w_seeds = pd.read_csv(w_seeds_file)
    df_submission = pd.read_csv(submission_file)
except FileNotFoundError as e:
    print(f"Dosya bulunamadı: {e}")
    raise
df_regular = pd.concat([
    df_m_regular.assign(Gender='M'),
    df_w_regular.assign(Gender='W')
], ignore_index=True)
df_tourney = pd.concat([
    df_m_tourney.assign(Gender='M'),
    df_w_tourney.assign(Gender='W')
], ignore_index=True)
df_seeds = pd.concat([
    df_m_seeds.assign(Gender='M'),
    df_w_seeds.assign(Gender='W')
], ignore_index=True)
print(f"Düzenli sezon verisi: {df_regular.shape}")
print(f"Turnuva verisi: {df_tourney.shape}")
print(f"Seed verisi: {df_seeds.shape}")
print(f"Submission verisi: {df_submission.shape}")  
def calculate_elo_ratings(df, initial_elo=1500, k_factor=20):
    elo_ratings = {}
    for team in set(df['WTeamID']).union(df['LTeamID']):
        elo_ratings[team] = initial_elo
    for idx, row in tqdm(df.iterrows(), total=df.shape[0], desc="Elo hesaplanıyor"):
        winner, loser = row['WTeamID'], row['LTeamID']
        elo_w, elo_1 = elo_ratings[winner], elo_ratings[loser]
        expected_w = 1/ (1 + 10 ** ((elo_1 - elo_w) / 400))
        elo_ratings[winner] += k_factor * (1- expected_w)
        elo_ratings[loser] += k_factor * (0 - (1- expected_w))
    return elo_ratings
df_seeds['SeedNum'] = df_seeds['Seed'].str.extract('(\d+)').astype(int)
def preprocess_data(df, elo_ratings=None, seeds_df=None, fit=False, is_train=True):
    df_processed = df.copy()

    if is_train:
        df_processed['TeamA'] = df_processed['WTeamID']
        df_processed['TeamB'] = df_processed['LTeamID']
        df_processed['Result'] = 1
        df_reverse = df_processed.copy()
        df_reverse['TeamA'] = df_processed['LTeamID']
        df_reverse['TeamB'] = df_processed['WTeamID']
        df_reverse['Result'] = 0
        df_processed = pd.concat([df_processed, df_reverse], ignore_index=True)
    if fit:
        elo_ratings = calculate_elo_ratings(df)

    df_processed['EloA'] = df_processed['TeamA'].map(elo_ratings)
    df_processed['EloB'] = df_processed['TeamB'].map(elo_ratings)
    df_processed['EloDiff'] = df_processed['EloA'] - df_processed['EloB']

    seeds_df_team_a = seeds_df.rename(columns={'TeamID': 'TeamA', 'SeedNum': 'SeedA'})
    seeds_df_team_b = seeds_df.rename(columns={'TeamID': 'TeamB', 'SeedNum': 'SeedB'})
    df_processed = df_processed.merge(seeds_df_team_a[['Season', 'TeamA', 'SeedA']], on=['Season', 'TeamA'], how='left')
    df_processed = df_processed.merge(seeds_df_team_b[['Season', 'TeamB', 'SeedB']], on=['Season', 'TeamB'], how='left')
    df_processed['SeedDiff'] = df_processed['SeedA'] - df_processed['SeedB']
    df_processed['SeedDiff'] = df_processed['SeedDiff'].fillna(0)

    features = ['EloDiff', 'SeedDiff']
    if fit:
        return df_processed[features], df_processed['Result'], elo_ratings
    else:
        return df_processed[features], elo_ratings
df_test = df_submission.copy()
df_test[['Season', 'TeamA', 'TeamB']] = df_test['ID'].str.split('_', expand=True).astype(int)
print("\nEğitim verisi ön işleniyor...")
X_train, y_train, elo_ratings = preprocess_data(df_tourney, seeds_df=df_seeds, fit=True, is_train=True)
X_test, _ = preprocess_data(df_test, elo_ratings=elo_ratings, seeds_df=df_seeds, fit=False, is_train=False)

print(f"X_train şekli: {X_train.shape}")
print(f"y_train şekli: {y_train.shape}")
print(f"X_test şekli: {X_test.shape}")

Veri setleri yükleniyor...
Düzenli sezon verisi: (329125, 9)
Turnuva verisi: (4168, 9)
Seed verisi: (4234, 4)
Submission verisi: (507108, 2)

Eğitim verisi ön işleniyor...


Elo hesaplanıyor: 100%|██████████| 4168/4168 [00:00<00:00, 18899.63it/s]


X_train şekli: (8336, 2)
y_train şekli: (8336,)
X_test şekli: (507108, 2)


In [3]:
import pandas as pd
import numpy as np
from sklearn.model_selection import StratifiedKFold, cross_val_score
from sklearn.metrics import brier_score_loss
from xgboost import XGBClassifier
from catboost import CatBoostClassifier
from lightgbm import LGBMClassifier
from sklearn.ensemble import StackingClassifier
import optuna
def objective(trial, model_name, X, y):
    if model_name == 'xgb':
        params = {
            'n_estimators': trial.suggest_int('n_estimators', 100, 500),
            'max_depth': trial.suggest_int('max_depth', 3, 10),
            'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
            'subsample': trial.suggest_float('subsample', 0.6, 1.0),
            'colsample_bytree': trial.suggest_float('colsample_bytree', 0.6, 1.0),
            'random_state': 42
        }
        model = XGBClassifier(**params)
    elif model_name == 'lgbm':
        params = {
            'n_estimators': trial.suggest_int('n_estimators', 100, 500),
            'max_depth': trial.suggest_int('max_depth', 3, 10),
            'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
            'subsample': trial.suggest_float('subsample', 0.6, 1.0),
            'colsample_bytree': trial.suggest_float('colsample_bytree', 0.6, 1.0),
            'random_state': 42
        }
        model = LGBMClassifier(**params)
    elif model_name == 'catboost':
        params = {
            'iterations': trial.suggest_int('iterations', 100, 500),
            'depth': trial.suggest_int('depth', 3, 10),
            'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
            'random_state': 42,
            'verbose': False
        }
        model = CatBoostClassifier(**params)
    scores = cross_val_score(model, X, y, cv=5, scoring='roc_auc')
    return scores.mean()
print("\nHiperparametre optimizasyonu başlıyor...")
best_params = {}
for name in ['xgb', 'lgbm', 'catboost']:
    study = optuna.create_study(direction='maximize')
    study.optimize(lambda trial: objective(trial, name, X_train, y_train), n_trials=50)
    print(f"\n{name} için en iyi parametreler: {study.best_params}")
    print(f"\n{name} için en iyi ROC AUC: {study.best_value:.4f}")
    best_params[name] = study.best_params

[I 2025-03-15 09:16:15,318] A new study created in memory with name: no-name-1af0d8a0-afbd-4e7c-87ac-d1b5b019cf68



Hiperparametre optimizasyonu başlıyor...


[I 2025-03-15 09:16:16,328] Trial 0 finished with value: 0.8236526774331354 and parameters: {'n_estimators': 441, 'max_depth': 3, 'learning_rate': 0.24023612863157442, 'subsample': 0.9304464025706055, 'colsample_bytree': 0.988395026886181}. Best is trial 0 with value: 0.8236526774331354.
[I 2025-03-15 09:16:17,634] Trial 1 finished with value: 0.8189222059784699 and parameters: {'n_estimators': 322, 'max_depth': 7, 'learning_rate': 0.2992073097516932, 'subsample': 0.8359595593792298, 'colsample_bytree': 0.7374143125306722}. Best is trial 0 with value: 0.8236526774331354.
[I 2025-03-15 09:16:18,519] Trial 2 finished with value: 0.8244919170849678 and parameters: {'n_estimators': 383, 'max_depth': 3, 'learning_rate': 0.2901780147837727, 'subsample': 0.6239928348041113, 'colsample_bytree': 0.6658565941568888}. Best is trial 2 with value: 0.8244919170849678.
[I 2025-03-15 09:16:19,609] Trial 3 finished with value: 0.82396936173845 and parameters: {'n_estimators': 370, 'max_depth': 4, 'lear


xgb için en iyi parametreler: {'n_estimators': 113, 'max_depth': 3, 'learning_rate': 0.048256823217894616, 'subsample': 0.6202931544702613, 'colsample_bytree': 0.9885855911011476}

xgb için en iyi ROC AUC: 0.8312
[LightGBM] [Info] Number of positive: 3334, number of negative: 3334
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003025 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 284
[LightGBM] [Info] Number of data points in the train set: 6668, number of used features: 2
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive

[I 2025-03-15 09:17:05,029] Trial 0 finished with value: 0.7842292050267305 and parameters: {'n_estimators': 431, 'max_depth': 10, 'learning_rate': 0.2984641586719442, 'subsample': 0.6675622063812786, 'colsample_bytree': 0.9535136749257267}. Best is trial 0 with value: 0.7842292050267305.


...

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Info] Number of positive: 3334, number of negative: 3334
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000341 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 284
[LightGBM] [Info] Number of data points in the train set: 6668, number of used features: 2
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits wi

[I 2025-03-15 09:17:51,310] Trial 49 finished with value: 0.8297898470327869 and parameters: {'n_estimators': 119, 'max_depth': 4, 'learning_rate': 0.05387897131266356, 'subsample': 0.9622855408156544, 'colsample_bytree': 0.6306649149527357}. Best is trial 46 with value: 0.8306988689235506.
[I 2025-03-15 09:17:51,312] A new study created in memory with name: no-name-692e1ce5-351e-4ad5-9bde-df1b070521c2


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2025-03-15 09:17:56,498] Trial 0 finished with value: 0.8316231243804391 and parameters: {'iterations': 417, 'depth': 4, 'learning_rate': 0.010907440396377836}. Best is trial 0 with value: 0.8316231243804391.
[I 2025-03-15 09:18:07,541] Trial 1 finished with value: 0.8237002395458124 and parameters: {'iterations': 296, 'depth': 10, 'learning_rate': 0.06138643122598118}. Best is trial 0 with value: 0.8316231243804391.
[I 2025-03-15 09:18:15,766] Trial 2 finished with value: 0.8119931898712249 and parameters: {'iterations': 401, 'depth': 8, 'learning_rate': 0.13455244127378224}. Best is trial 0 with value: 0.8316231243804391.
[I 2025-03-15 09:18:19,109] Trial 3 finished with value: 0.8295594155057604 and parameters: {'iterations': 260, 'depth': 4, 'learning_rate': 0.07432381553934628}. Best is trial 0 with value: 0.8316231243804391.
[I 2025-03-15 09:18:20,567] Trial 4 finished with value: 0.8316781459577604 and parameters: {'iterations': 159, 'depth': 6, 'learning_rate': 0.05809116447


catboost için en iyi parametreler: {'iterations': 385, 'depth': 5, 'learning_rate': 0.014357042485570397}

catboost için en iyi ROC AUC: 0.8317


In [4]:
base_models = [
    ('xgb', XGBClassifier(**best_params['xgb'])),
    ('lgbm', LGBMClassifier(**best_params['lgbm'])),
    ('catboost', CatBoostClassifier(**best_params['catboost'], verbose=False))
]
stacking_model = StackingClassifier(
    estimators= base_models,
    final_estimator=XGBClassifier(random_state=42),
    cv=5
)
skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
final_predictions = np.zeros(len(X_test))
train_brier_scores = []
print("\nk-Fold ile eğitim ve tahmin yapılıyor...")
for fold, (train_idx, val_idx) in enumerate(skf.split(X_train, y_train)):
    X_fold_train, X_fold_val = X_train.iloc[train_idx], X_train.iloc[val_idx]
    y_fold_train, y_fold_val = y_train.iloc[train_idx], y_train.iloc[val_idx]

    stacking_model.fit(X_fold_train, y_fold_train)
    val_pred = stacking_model.predict_proba(X_fold_val)[:, 1]
    brier_score = brier_score_loss(y_fold_val, val_pred)
    train_brier_scores.append(brier_score)
    print(f"Fold {fold+1} Brier Score: {brier_score:.4f}")

    test_pred = stacking_model.predict_proba(X_test)[:, 1]
    final_predictions += test_pred / 5
print(f"Ortalama Eğitim Brier Score: {np.mean(train_brier_scores):.4f}")
submission = pd.DataFrame({
    'ID': df_submission['ID'],
    'Pred': final_predictions
})
submission.to_csv('/kaggle/working/submission.csv', index=False)
print("\nSubmission dosyası oluşturuldu: /kaggle/working/submission.csv")
cv_scores = cross_val_score(stacking_model, X_train, y_train, cv=5, scoring='roc_auc')
print(f"\nStacking Model ROC AUC: {cv_scores.mean():.4f}, Std: {cv_scores.std():.4f}")


k-Fold ile eğitim ve tahmin yapılıyor...
[LightGBM] [Info] Number of positive: 3334, number of negative: 3334
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000175 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 284
[LightGBM] [Info] Number of data points in the train set: 6668, number of used features: 2
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf